Notebook reprenant tabular_datas_map_v3.ipynb avec implementation rapide essai isochrones

API 
    * mapbox (je laisse mon token dans le code mais la creation de comptes est gratuite)


A faire

    - voir aux layers
    - voir warning slice dataframe

In [1]:
# from tqdm.notebook import tqdm
from tqdm import tqdm

import os
os.environ['USE_PYGEOS'] = '0'

# Data management
import pandas as pd
import geopandas as gpd
import numpy as np


# Visualisation
import matplotlib.pyplot as plt
import seaborn as sns
import folium
from folium.features import Choropleth
from folium.plugins import MarkerCluster

# Preprocessing
from sklearn.preprocessing import StandardScaler
import umap


# I/O
import gc
import io, requests
import zipfile, shutil
import joblib

# tqdm().pandas()

# data_path = 'C:/Users/demo/Desktop/Lattitude/datas/'
data_path = 'datas'
os.makedirs(data_path, exist_ok=True)

c:\Users\demo\miniconda3\envs\E-Motion\lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


------------------------------------------------

# Datas

In [2]:
# Load the data for French garge points
file_name = 'dataset_charge_points.feather'

bornes = gpd.read_feather(os.path.join(data_path, file_name))

# Load the data for the communes
file_name = 'dataset_communes.feather'

communes = gpd.read_feather(os.path.join(data_path, file_name))

In [ ]:
bornes.crs 

-------------------------------------------------------

# Create some metric on electrics stuff

In [32]:
communes['VE_pct'] = communes.nb_vp_rechargeables_el / communes.nb_vp
communes['VE_per_inhab'] = communes.nb_vp_rechargeables_el / communes.PMUN
communes['VE_per_ha'] = communes.nb_vp_rechargeables_el / communes.surf_ha


----------------------------

# Select a town

In [3]:
TOWN = 'Reims'

In [25]:
def single_popup(df):
    texts = []

    # loop on rows
    for index, row in df.iterrows():
        text = ''
        for col in communes_info_cols:
            text += f'<b>{col}:</b> {row[col]}<br>'
        texts.append(text)
    return texts    

# list of columns from datas_ to be displayed
communes_info_cols = communes.columns.tolist()
communes_info_cols.remove('geometry')
communes_info_cols.remove('wikipedia')


# communes['html_popup'] = popup(communes)   
# communes.html_popup.head(2)

In [28]:
# Column names generator 
def split_list(list_a, chunk_size):
  for i in range(0, len(list_a), chunk_size):
    yield list_a[i:i + chunk_size]


def column_popup(df, info_cols,num_cols=3,width=20):
    # Mise en page
    num_cols = 3
    width = 20
    px = np.ceil(width / num_cols / 2)

    texts = []

    # Loop on rows
    for index, row in df.iterrows():
        text = f'<table style="width:{width}%"><tr>'
        # Create header
        for n in range(num_cols):
          text += f'<td style="font-weight:bold">{n}</td>'
        # lines
        for cols in split_list(bornes_info_cols,num_cols):
                text += '<tr>'
                for col in cols:
                        text += f'<th style="width:{px}%"><b>{col}:</b><br> {row[col]}</th>' 
                text  += '</tr>'
        # ends table         
        text += '</table>'
        # append to previous
        texts.append(text)
    
    return texts

 # list of columns from datas_ to be displayed
bornes_info_cols = bornes.columns.tolist()
bornes_info_cols.remove('geometry')   


# bornes_1['html_popup'] = column_popup(bornes_1, info_cols=bornes_info_cols)   
# bornes_1.html_popup.head(2)

------------------------------------------------

# Map

In [34]:
from branca.colormap import linear, LinearColormap

# Define the color map
colors = [ 'red', 'green', 'blue']
bins = np.array([0, 1, 5, 10, 25, 50, 100]) / 100

labels = [1,2,3,4,5,6]

cmap = LinearColormap(colors=colors, vmin=1, vmax=6)

'''color argument of Icon should be one of: 
{'red', 'darkred', 'gray', 'blue', 'black', 'darkpurple', 'white', 'darkblue', 
 'purple', 'lightred', 'green', 'orange', 'cadetblue', 'beige', 'lightblue', 
 'lightgray', 'darkgreen', 'pink', 'lightgreen'}.'''
icon_labels = ['darkred','lightred','lightgreen','darkgreen','lightblue','blue']

# Function to make a column color 
def make_color(df, col='VE_per_inhab', color_type=None):
    if color_type:
        color =pd.cut( df[col], #.apply(lambda x:  x ** (1/3)),
                        bins=bins, 
                        labels=icon_labels)
    else:
        color =pd.cut( df[col], #.apply(lambda x:  x ** (1/3)),
                            bins=bins, 
                            labels=labels).apply(cmap)
    return color

def make_color_by_date(df, date_col='date_arrete', col='VE_per_inhab', color_type=None, icons=None):
    if icons:
        df['color'] = 'white'
    else:
        df['color'] = '#000000'

    for date in df[date_col].unique():
        df.loc[df[date_col] == date,'color'] = make_color(df.loc[df[date_col] == date], col, icons)
    
    return df


# display(make_color_by_date(communes, 'VE_per_inhab').color.value_counts())  # trés long sur toute la base

# display(make_color_by_date(communes, 'VE_per_inhab', icons='ok').color.value_counts())    




In [45]:
'''
icons from https://fontawesome.com/v4/icons/

'''
from folium.plugins import MarkerCluster
import math


def make_map(df,com_df, pdc_df, color_col='VE_per_inhab', info_cols=bornes_info_cols):
    # Get center
    center = df.iloc[0,1]
    
    # Create a folium map centered on the town_
    m = folium.Map(location=[center.y, center.x], zoom_start=10, crs='EPSG3857')

    
    # cluster_isochrones = MarkerCluster(name='colors')

    # Create colors by binning the VE_per_inhab column
    # com_df = make_color_by_date(com_df, 'VE_per_inhab',icons='XXX')    

    # communes markers
    for index, row in df.iterrows():
        # style the polygons based on "values" property
        # color = cmap(row.VE_per_inhab ** (1/3))
        def style_fn(feature):
            ss = {
                "fillColor": 'blue',
                "fillOpacity": 0.09,
                "weight": 0.3,
                "color": 'black',
            }
            # print(row['style'], end='   ')
            return ss   #row['style']
        if index > 0:    
            folium.GeoJson(row.geometry, style_function=style_fn
                                ).add_to(m)
        # print('done')   
        if index == 1:
            mask = row.geometry                     
        del style_fn

    # Take POI in larger isochrone
    com_df = com_df[com_df.within(mask)]
    com_df['html_popup'] = single_popup(com_df)
    pdc_df = pdc_df[pdc_df.within(mask)]
    pdc_df['html_popup'] = column_popup(pdc_df, info_cols=info_cols) 

    # Create a marker cluster layer for the data
    cluster_com = MarkerCluster(name='Communes', )

    # communes markers
    for index, row in com_df.iterrows():
        #communes child markers
        popup = folium.Popup(row.html_popup, parse_html=False)
        cluster_com.add_child(folium.Marker(location=[
                                                    row.geometry.centroid.y,
                                                    row.geometry.centroid.x
                                                ], 
                                            popup=popup, 
                                            tooltip=row.date_arrete,   #.strftime('%d/%m/%Y'),
                                            icon=folium.Icon(
                                                        prefix='fa', 
                                                        icon='institution', 
                                                        color=row.color
                                                        )
                                            )
        )
        
        
    cluster_com.add_to(m)

    # Create a marker cluster layer for the data
    cluster_bdr = MarkerCluster(name='Points de charge')

    # bornes markers
    for index, row in pdc_df.iterrows():
        popup = folium.Popup(row.html_popup, parse_html=False)
        cluster_bdr.add_child(folium.Marker(location=[row.geometry.y, row.geometry.x], 
                                            popup=popup, 
                                            tooltip='pdc infos',
                                            icon=folium.Icon(prefix='fa', icon='bolt', color='blue')))
        
    cluster_bdr.add_to(m)

    # Add a layer control to the map
    folium.LayerControl().add_to(m)

    return m

# m = make_map(centre_df, bornes_1)

# display(m)



In [9]:
origin = communes.query("nom == @TOWN").iloc[0].geometry.centroid

d = {'name': ['reims'], 
     'geometry': [origin], 
     'style': [
        {
            'fill': 'black',
            'fillOpacity': 1.0,
            'fill-opacity': 0.33,
            'fillColor': 'black',
            'color': 'black',
            'contour': 0,
            'opacity': 1.0,
            'weight': 10,
            'metric': 'distance'
        }
             ]
}


In [36]:
token = 'pk.eyJ1IjoibWlrYWxlcm95IiwiYSI6ImNsZzZvcDN4dDBmbXMzZHFmYmd1ajJ6bGIifQ.-GfBZA2ZGXHpkELd0eLBAw'

In [37]:
iso1 = 10000
iso2 = 20000
iso3 = 30000
iso4 = 40000

request = f'https://api.mapbox.com/isochrone/v1/mapbox/driving/'\
    + f'{origin.x}%2C{origin.y}?'\
    + f'contours_meters={iso1}%2C{iso2}%2C{iso3}%2C{iso4}'\
    + f'&polygons=true&denoise=1&access_token={token}'

In [38]:
isos = requests.get(request).json()   
# isos.keys()

In [39]:
from shapely.geometry import Polygon, Point

In [40]:

for i, feature in enumerate(isos['features']):
    # print(i,feature['geometry']['coordinates'][0])
    points = [ Point(point) for point in feature['geometry']['coordinates'][0] ]
    # print(points)
    # print(Polygon(points))
    d['name'].append(f'iso_{i}')
    d['geometry'].append( Polygon( points ))
    style = feature['properties']
    style.pop('fill-opacity')
    style.pop('fill')
    style.pop('contour')
    style.pop('metric')
    d['style'].append(feature['properties'])

    # break

In [41]:
centre_df = gpd.GeoDataFrame(d, crs='EPSG:3857')    #"EPSG:4326")
centre_df

name                                           geometry  \
0  reims                               POINT (4.043 49.251)   
1  iso_0  POLYGON ((4.055 49.570, 4.047 49.567, 4.050 49...   
2  iso_1  POLYGON ((4.041 49.481, 4.040 49.476, 4.035 49...   
3  iso_2  POLYGON ((4.097 49.416, 4.096 49.414, 4.094 49...   
4  iso_3  POLYGON ((4.073 49.333, 4.071 49.334, 4.070 49...   
5  iso_0  POLYGON ((4.055 49.570, 4.047 49.567, 4.050 49...   
6  iso_1  POLYGON ((4.041 49.481, 4.040 49.476, 4.035 49...   
7  iso_2  POLYGON ((4.097 49.416, 4.096 49.414, 4.094 49...   
8  iso_3  POLYGON ((4.073 49.333, 4.071 49.334, 4.070 49...   

                                               style  
0  {'fill': 'black', 'fillOpacity': 1.0, 'fill-op...  
1  {'fillOpacity': 0.33, 'fillColor': '#bf4040', ...  
2  {'fillOpacity': 0.33, 'fillColor': '#bf8f40', ...  
3  {'fillOpacity': 0.33, 'fillColor': '#9fbf40', ...  
4  {'fillOpacity': 0.33, 'fillColor': '#50bf40', ...  
5  {'fillOpacity': 0.33, 'fillColor': '#bf4040', ...  
6  {'fillOpacity': 0.33, 'fillColor': '#bf8f40', ...  
7  {'fillOpacity': 0.33, 'fillColor': '#9fbf40', ...  
8  {'fillOpacity': 0.33, 'fillColor': '#50bf40', ...

In [46]:
make_map(centre_df, communes, bornes)

c:\Users\demo\miniconda3\envs\E-Motion\lib\site-packages\geopandas\geodataframe.py:1443: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super().__setitem__(key, value)
c:\Users\demo\miniconda3\envs\E-Motion\lib\site-packages\geopandas\geodataframe.py:1443: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super().__setitem__(key, value)
C:\Users\demo\AppData\Local\Temp\ipykernel_29792\307653469.py:62: UserWarning: color argument of Icon should be one of: {'darkgreen', 'gray', 'red', 'darkblue', 'orange', 'purple